# Deploy a custom application with Pulumi

This notebook outlines how to use Pulumi to deploy a custom application in two easy steps.

## Initialize the environment

In [1]:
import os

import datarobot as dr

os.environ["PULUMI_CONFIG_PASSPHRASE"] = "default"

assert (
    "DATAROBOT_API_TOKEN" in os.environ
), "Please set the DATAROBOT_API_TOKEN environment variable"
assert "DATAROBOT_ENDPOINT" in os.environ, "Please set the DATAROBOT_ENDPOINT environment variable"

dr.Client()

## Set up a project

Configure the functions below to create and build or destroy the Pulumi stack.

In [2]:
from pulumi import automation as auto


def stack_up(project_name: str, stack_name: str, program: callable) -> auto.Stack:
    # create (or select if one already exists) a stack that uses our inline program
    stack = auto.create_or_select_stack(
        stack_name=stack_name, project_name=project_name, program=program
    )

    stack.refresh(on_output=print)

    stack.up(on_output=print)
    return stack


def destroy_project(stack: auto.Stack):
    """Destroy pulumi project"""
    stack_name = stack.name
    stack.destroy(on_output=print)

    stack.workspace.remove_stack(stack_name)
    print(f"stack {stack_name} in project removed")

## 2. Declarative App Deployment

To deploy a custom application, you have to put your source code onto DataRobot and initialize the deployment. The `make_custom_application` function below shows the declarative way to do this.

In [3]:
import pulumi
import pulumi_datarobot as datarobot


def make_custom_application():
    """Make a custom app on DataRobot.

    Upload source code to create source. Then initialize application.
    """

    file_mapping = [
        ("frontend/app.py", "app.py"),
        ("frontend/requirements.txt", "requirements.txt"),
        ("frontend/start-app.sh", "start-app.sh"),
    ]

    app_source = datarobot.ApplicationSource(
        resource_name="App Template Minis - Custom App Source",
        files=file_mapping,
        base_environment_id="6542cd582a9d3d51bf4ac71e",  # Python 3.9 streamlit environment
    )

    app = datarobot.CustomApplication(
        resource_name="App Template Minis - Custom App",
        source_version_id=app_source.version_id,
    )
    pulumi.export("Application Source Id", app_source.id)
    pulumi.export("Application Id", app.id)
    pulumi.export("Application Url", app.application_url)

## Run the stack

Running the stack takes the files that are in the `frontend` directory, puts them onto DataRobot, and initializes the application.

In [ ]:
project_name = "AppTemplateMinis-CustomApplications"
stack_name = "MarshallsCustomApplicationDeployer"

stack = stack_up(project_name, stack_name, program=make_custom_application)

### Interact with outputs

In [ ]:
import webbrowser

outputs = stack.outputs()
app_url = outputs.get("Application Url").value
webbrowser.open(app_url)

## Clear your work

Use the following cell to shut down the stack, thereby deleting any assets created in DataRobot.

In [ ]:
destroy_project(stack)